In [150]:
import pandas as pd

df_counties = pd.read_stata("USA_Counties_cnty_panel_modified.dta", convert_missing=False)

df_filtered = df_counties[(df_counties['year'] == 2001) | (df_counties['year'] == 2007)]
df_filtered = df_filtered[df_filtered['counname'] != "YELLOWSTONE N.P."]
df_filtered.reset_index(drop=True, inplace=True)




In [151]:
df_filtered



fips  level  statefip  stateicp  counicp  year  counname statename  \
0      1001      1         1        41     10.0  2001   AUTAUGA   ALABAMA   
1      1001      1         1        41     10.0  2007   AUTAUGA   ALABAMA   
2      1003      1         1        41     30.0  2001   BALDWIN   ALABAMA   
3      1003      1         1        41     30.0  2007   BALDWIN   ALABAMA   
4      1005      1         1        41     50.0  2001   BARBOUR   ALABAMA   
...     ...    ...       ...       ...      ...   ...       ...       ...   
6285  56041      1        56        68    410.0  2007     UINTA   WYOMING   
6286  56043      1        56        68    430.0  2001  WASHAKIE   WYOMING   
6287  56043      1        56        68    430.0  2007  WASHAKIE   WYOMING   
6288  56045      1        56        68    450.0  2001    WESTON   WYOMING   
6289  56045      1        56        68    450.0  2007    WESTON   WYOMING   

      afn110    afn120  ...  wtn150  wtn160  wtn170  wtn210    wtn220  \
0        NaN       NaN  ...     NaN     NaN     NaN     NaN       NaN   
1       92.0   88157.0  ...     NaN     NaN     NaN    26.0       0.0   
2        NaN       NaN  ...     NaN     NaN     NaN     NaN       NaN   
3      414.0  436955.0  ...     NaN     NaN     NaN   183.0       0.0   
4        NaN       NaN  ...     NaN     NaN     NaN     NaN       NaN   
...      ...       ...  ...     ...     ...     ...     ...       ...   
6285    51.0   35497.0  ...     NaN     NaN     NaN    28.0  159375.0   
6286     NaN       NaN  ...     NaN     NaN     NaN     NaN       NaN   
6287    33.0   10175.0  ...     NaN     NaN     NaN    10.0   12128.0   
6288     NaN       NaN  ...     NaN     NaN     NaN     NaN       NaN   
6289    29.0    7520.0  ...     NaN     NaN     NaN     6.0   11540.0   

       wtn230  wtn240   wtn250   wtn260   wtn270  
0         NaN     NaN      NaN      NaN      NaN  
1         0.0     0.0      0.0      0.0      0.0  
2         NaN     NaN      NaN      NaN      NaN  
3         0.0     0.0      0.0      0.0      0.0  
4         NaN     NaN      NaN      NaN      NaN  
...       ...     ...      ...      ...      ...  
6285  12334.0   225.0  22057.0  12179.0  12954.0  
6286      NaN     NaN      NaN      NaN      NaN  
6287   1992.0    69.0   2893.0    842.0    945.0  
6288      NaN     NaN      NaN      NaN      NaN  
6289   2083.0    51.0   2472.0   1355.0   1409.0  

[6290 rows x 1707 columns]

In [145]:
median_age_values = {'age130': 2.5, 'age160': 7, 'age230': 12, 'age260': 17, 'age340': 22, 'age370':27, 'age430':32, 'age460':37, 'age530':42,'age560':47, 'age630':52,'age660':57,'age690':62,'age730':67, 'age800':72, 'age830':77, 'age870':82, 'age900': 85}






0.5012917165946931

In [153]:

import numpy as np
# 2.5, 7, 12, 17, 22, 27, 32, 37, 42, 47, 52, 57, 62, 67, 72, 77, 82

def weightedAge(row, prev_row):
    weighted_age_2001 = 0
    weighted_age_2007 = 0

    for age_group in median_age_values:
        weighted_age_2001 += prev_row[age_group] * median_age_values[age_group]
        weighted_age_2007 += row[age_group] * median_age_values[age_group]

    if (row['age040'] == 0 or prev_row['age040'] == 0):
        return 0
    weighted_age_2007 /= row['age040']
    weighted_age_2001 /= prev_row['age040']

    weighted_age_delta = weighted_age_2007 - weighted_age_2001

    return weighted_age_delta

df_filtered['hc_ind_share'] = df_filtered['emn350']/df_filtered['emn010']


#print(df_filtered['hc_ind_share'])

#Make a new dataframe that has just the counties and deltas
new_df = df_filtered[['counname']].drop_duplicates()
new_df.reset_index(drop=True, inplace=True)
new_df['hc_delta'] = np.nan
new_df['age_delta'] = np.nan
count = 0 
for index,row in df_filtered.iterrows():
    year = row['year']
    if year == 2007:
        prev_row = df_filtered.iloc[index-1]
        new_hc_value = row['hc_ind_share'] - df_filtered.loc[index-1, 'hc_ind_share']
        new_df['hc_delta'][count] = new_hc_value
        new_df['age_delta'][count] = weightedAge(row, prev_row)
        count += 1




/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/732229605.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['hc_delta'][count] = new_hc_value
/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/732229605.py:38: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['age_delta'][count] = weightedAge(row, prev_row)
/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/732229605.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/index

        counname  hc_delta  age_delta
0        AUTAUGA  0.070356   0.501292
1        BALDWIN  0.012475   0.840811
2        BARBOUR -0.011611   1.269183
3           BIBB  0.000000   1.341824
4         BLOUNT  0.061434   1.209850
...          ...       ...        ...
1841    SUBLETTE  0.003789   1.337024
1842  SWEETWATER  0.001684   1.063506
1843       UINTA -0.002049   1.734482
1844    WASHAKIE  0.148838   1.502151
1845      WESTON  0.011323   1.069356

[1846 rows x 3 columns]


/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/732229605.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['hc_delta'][count] = new_hc_value
/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/732229605.py:38: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['age_delta'][count] = weightedAge(row, prev_row)
/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/732229605.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/index

In [155]:
import math 
#'age130': <5, 'age160': 5-9 'age230': 10-14, 'age260': 15-19, 'age290': <18, 'age340': 20-24, 'age370': 25-29, 'age430': 30-34, 'age460': 35-39, 'age530': 40-44,'age560': 45-49, 'age630': 50-54,'age660': 55-59,'age690': 60-64,'age730': 65-69,'age770': >65, 'age800': 70-74, 'age830': 75-79, 'age870': 80-84}
# 2.5, 7, 12, 17, 22, 27, 32, 37, 42, 47, 52, 57, 62, 67, 72, 77, 82

ageList2001 = {'age130': 0, 'age160': 0, 'age230':0, 'age260':0, 'age340':0, 'age370':0, 'age430':0, 'age460':0, 'age530':0,'age560':0, 'age630':0,'age660':0,'age690':0,'age730':0, 'age800':0, 'age830':0, 'age870':0, 'age900':0}
ageList2007= {'age130': 0, 'age160': 0, 'age230':0, 'age260':0,  'age340':0, 'age370':0, 'age430':0, 'age460':0, 'age530':0,'age560':0, 'age630':0,'age660':0,'age690':0,'age730':0, 'age800':0, 'age830':0, 'age870':0, 'age900':0}

yearlist = ['2000','2001', '2002', '2003', '2004', '2005', '2007', '2008']
age130_total = 0


count = 0 
for index,row in df_filtered.iterrows():
    ageVal = row['age130']
    year = row['year']
    if ((not math.isnan(ageVal)) and (type(ageVal) == int or type(ageVal) == float)):
        if (year == 2001):
            for key in ageList2001:
                ageList2001[key] += row[key]
                #get the total share 
        elif (year == 2007):
            for key in ageList2007:
                ageList2007[key] += row[key]



# age130Col = df_filtered['age130']
print(ageList2001)
print(ageList2007)

{'age130': 19430394.0, 'age160': 20237572.0, 'age230': 20898234.0, 'age260': 20369978.0, 'age340': 19801518.0, 'age370': 18898742.0, 'age430': 20685109.0, 'age460': 22244729.0, 'age530': 22820064.0, 'age560': 20694304.0, 'age630': 18649138.0, 'age660': 13930119.0, 'age690': 11101203.0, 'age730': 9528472.0, 'age800': 8813908.0, 'age830': 7466478.0, 'age870': 5157203.0, 'age900': 4354391.0}
{'age130': 20921289.0, 'age160': 20054444.0, 'age230': 20318855.0, 'age260': 21562382.0, 'age340': 21217108.0, 'age370': 21018332.0, 'age430': 19352724.0, 'age460': 20992716.0, 'age530': 21858105.0, 'age560': 22786678.0, 'age630': 20962479.0, 'age660': 18208990.0, 'age690': 14458648.0, 'age730': 10746312.0, 'age800': 8642992.0, 'age830': 7439268.0, 'age870': 5774217.0, 'age900': 5264356.0}


In [158]:
#Creating the rest of the instrument 

#Making the national 'shift' in the age 
nationalAgeDelta = {'age130': 0, 'age160': 0, 'age230':0, 'age260':0, 'age340':0, 'age370':0, 'age430':0, 'age460':0, 'age530':0,'age560':0, 'age630':0,'age660':0,'age690':0,'age730':0, 'age800':0, 'age830':0, 'age870':0, 'age900':0}
for age_group in nationalAgeDelta:
    nationalAgeDelta[age_group] = ageList2007[age_group] - ageList2001[age_group]

print(nationalAgeDelta)

{'age130': 1490895.0, 'age160': -183128.0, 'age230': -579379.0, 'age260': 1192404.0, 'age340': 1415590.0, 'age370': 2119590.0, 'age430': -1332385.0, 'age460': -1252013.0, 'age530': -961959.0, 'age560': 2092374.0, 'age630': 2313341.0, 'age660': 4278871.0, 'age690': 3357445.0, 'age730': 1217840.0, 'age800': -170916.0, 'age830': -27210.0, 'age870': 617014.0, 'age900': 909965.0}


In [184]:
#New column for instrument

new_df['age_SS_instrument'] = np.nan
new_count = 0 
for index,row in df_filtered.iterrows():
    year = row['year']
    if year == 2001:
        total_share = 0
        for age_group in ageList2001:
            total_share += ((row[age_group] / ageList2001[age_group]) * nationalAgeDelta[age_group])
        new_df['age_SS_instrument'][new_count] = total_share
        new_count += 1



237.5562183659271
-31.761679711380395
-106.51493891780521
188.8999442218347
175.00498295130706
289.47227228140366
-199.74397451809412
-221.30703934401717
-160.31199899351728
320.1101174506763
345.59066622811196
716.3131321419437
603.3672904639254
201.81298323592702
-23.98744030457318
-3.1413766972861903
60.53845155988625
90.06883281726422
682.3602874445057
-86.09134494987838
-291.2387905600062
561.6656228101964
544.3884579959981
881.0903413571126
-587.8308647056199
-598.4633136685999
-487.1326480065963
1086.3117820246575
1245.6645621904884
2649.928555312413
2300.9615768669396
872.1797324901621
-115.69043561607404
-16.913142983880753
354.9754659647875
475.63030972643475
144.55940419942075
-17.78111129141381
-59.99435914058576
125.73817173489337
142.6919713933043
221.61844634949776
-131.46644694983237
-129.78993711274254
-90.75775278281428
207.07060029658402
247.09856680775272
469.6581385270291
352.94718194055184
133.94553922181856
-19.081359142845603
-2.8644107703792874
62.4527108977482

/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/940142366.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['age_SS_instrument'][new_count] = total_share
/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/940142366.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['age_SS_instrument'][new_count] = total_share
/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/940142366.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gu

22.25171296063271
-3.158070147940672
-12.059864244988356
27.805228851989924
13.296947234045389
26.019979530912693
-16.682905320924345
-19.81182040923043
-18.800723521196083
39.937933162671236
46.020867613291294
97.67906347390141
87.40508618750599
47.162122111499095
-7.446384055744626
-1.1588837467946735
26.560348312835465
49.10945640848514
512.7868886755462
-61.41496302026744
-199.5560984722441
626.5249776902067
1174.7781392315478
762.318107205231
-423.64273473250734
-423.47766124730043
-330.0243597476326
741.1267090693169
756.5532926508453
1235.1179692721935
917.6021850965161
301.12184199103484
-38.99655816693344
-5.725177252246641
121.43582674562161
194.55703794170068
15.806389206518405
-1.8369290545328263
-7.319090024544657
21.60027251870375
6.862940507894395
20.18791515329433
-10.628105706380373
-13.001507143557468
-10.285597621461536
27.19823802723687
28.902593406730112
54.67570219608318
48.08791939035797
18.1491093220403
-2.365778267710532
-0.31340881202623244
8.255243394529941
1

/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/940142366.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['age_SS_instrument'][new_count] = total_share
/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/940142366.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['age_SS_instrument'][new_count] = total_share
/var/folders/2s/mhvlcrdj27nbd2gz33hjy9qr0000gn/T/ipykernel_48523/940142366.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gu

In [175]:
# pd.set_option('display.max_rows', 10000)  # Increase number of rows to display
# pd.set_option('display.max_columns', 10000) 
print(new_df)


                          counname  hc_delta  age_delta  age_SS_instrument
0                          AUTAUGA  0.070356   0.501292        2481.966443
1                          BALDWIN  0.012475   0.840811        9471.796154
2                          BARBOUR -0.011611   1.269183        1763.459229
3                             BIBB  0.000000   1.341824        1240.550626
4                           BLOUNT  0.061434   1.209850        3297.304014
5                          BULLOCK  0.088276  -0.146960         688.209697
6                           BUTLER -0.090391   0.640091        1373.406368
7                   CALHOUN/BENTON  0.002494   0.604227        7115.551638
8                         CHAMBERS  0.000000   1.279133        2380.501528
9                         CHEROKEE  0.004222   1.576695        1730.858204
10                   CHILTON/BAKER  0.066344   0.760175        2511.982561
11                         CHOCTAW  0.000000   1.966470        1075.890951
12                       

In [180]:
#Now make the regression
import statsmodels.api as sm
import linearmodels as lm
from linearmodels.iv import IV2SLS

y = new_df['hc_delta']
x = new_df['age_delta']
z = new_df['age_SS_instrument']
#model = sm.OLS(y, x).fit(cov_type='HC1')

model = lm.OLS(y, x)
results_OLS = model.fit(cov_type='robust')
print(results_OLS.summary)


#2SLS
age_instrument = IV2SLS(dependent=y,exog=None,      
             # Exogenous regressors
            endog=x,   # Endogenous regressor
            instruments=z)


results_2SLS = age_instrument.fit(cov_type='robust')


                            OLS Estimation Summary                            
Dep. Variable:               hc_delta   R-squared:                      0.0046
Estimator:                        OLS   Adj. R-squared:                 0.0041
No. Observations:                1842   F-statistic:                    10.165
Date:                Thu, Apr 18 2024   P-value (F-stat)                0.0014
Time:                        19:17:04   Distribution:                  chi2(1)
Cov. Estimator:                robust                                         
                                                                              
                             Parameter Estimates                              
            Parameter  Std. Err.     T-stat    P-value    Lower CI    Upper CI
------------------------------------------------------------------------------
age_delta      0.0022     0.0007     3.1883     0.0014      0.0008      0.0035


/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/linearmodels/iv/model.py:550: MissingValueWarning: 
Inputs contain missing values. Dropping rows with missing observations.
  super().__init__(
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/linearmodels/iv/model.py:550: MissingValueWarning: 
Inputs contain missing values. Dropping rows with missing observations.
  super().__init__(


In [181]:
print(results_2SLS.summary)

                          IV-2SLS Estimation Summary                          
Dep. Variable:               hc_delta   R-squared:                     -0.0259
Estimator:                    IV-2SLS   Adj. R-squared:                -0.0264
No. Observations:                1842   F-statistic:                    130.24
Date:                Thu, Apr 18 2024   P-value (F-stat)                0.0000
Time:                        19:17:04   Distribution:                  chi2(1)
Cov. Estimator:                robust                                         
                                                                              
                             Parameter Estimates                              
            Parameter  Std. Err.     T-stat    P-value    Lower CI    Upper CI
------------------------------------------------------------------------------
age_delta      0.0077     0.0007     11.412     0.0000      0.0064      0.0090

Endogenous: age_delta
Instruments: age_SS_instrumen